## RQ1 

#### Dataset organization

In [22]:
import networkx as nx
import pandas as pd
import collections

In [2]:
wiki_graph = pd.read_csv("wikigraph_reduced.csv", sep='\t')

In [3]:
wiki_graph.columns

Index(['Unnamed: 0', '0', '1'], dtype='object')

In [4]:
wiki_graph

Unnamed: 0        0        1
0              796       95  1185516
1              909      108  1059989
2              910      108  1062426
3              911      108  1161925
4             1141      134   541222
...            ...      ...      ...
483089    28511768  1791481  1060990
483090    28511769  1791481  1061382
483091    28511771  1791481  1110380
483092    28511772  1791482    80740
483093    28511785  1791484   235100

[483094 rows x 3 columns]

In [5]:
wiki_graph.rename(columns={'Unnamed: 0':'Edge ID',
                          '0':'Source Link',
                          '1':'Target Link'},
                 inplace=True)

In [6]:
#Wikigraph reduced DataFrame

wiki_graph = wiki_graph.set_index('Edge ID')

In [7]:
wiki_graph

Source Link  Target Link
Edge ID                           
796                95      1185516
909               108      1059989
910               108      1062426
911               108      1161925
1141              134       541222
...               ...          ...
28511768      1791481      1060990
28511769      1791481      1061382
28511771      1791481      1110380
28511772      1791482        80740
28511785      1791484       235100

[483094 rows x 2 columns]

In [8]:
#PageNames DataFrame

page_names = pd.read_csv('wiki-topcats-page-names.txt',names=['id'])
page_names[['id','name_of_page']] = page_names["id"].str.split(" ", 1, expand=True)
page_names["name_of_page"] = page_names["name_of_page"].str.strip("-")
page_names = page_names.set_index('id')
print(page_names)

                                    name_of_page
id                                              
0                              Chiasmal syndrome
1                                    Kleroterion
2                                       Pinakion
3        LyndonHochschildSerre spectral sequence
4                         Zariski's main theorem
...                                          ...
1791484           Noadiah Russell (Yale founder)
1791485                       Cornus officinalis
1791486                           Peter Grummitt
1791487                           Baron Estcourt
1791488                         Catherine Dubosc

[1791489 rows x 1 columns]


In [9]:
page_names.columns

Index(['name_of_page'], dtype='object')

In [10]:
#PagesPerCategory DataFrame

pages_per_categories = pd.read_csv('wiki-topcats-categories.txt',names=['cats'])
#pages_per_categories['cats'] = pages_per_categories["cats"].str.split(" ", expand=True)
pages_per_categories = pd.DataFrame(pages_per_categories.cats.str.split(' ', 1).tolist(), columns = ['cats','pages'])
pages_per_categories["cats"] = pages_per_categories["cats"].str.strip("-")
pages_per_categories['cats'] = pages_per_categories['cats'].str.replace("Category:", "")
pages_per_categories['cats'] = pages_per_categories['cats'].str.replace(";", "")
pages_per_categories['cats'] = pages_per_categories['cats'].str.replace("_", " ")

print(pages_per_categories)

                                                  cats  \
0                                         Buprestoidea   
1                                People from Worcester   
2      Skin conditions resulting from physical factors   
3                                     Visual kei bands   
4                           Japanese rock music groups   
...                                                ...   
17359                   British science fiction novels   
17360                           Television soundtracks   
17361                         Diptera of North America   
17362                                  Diptera of Asia   
17363                                       Tachinidae   

                                                   pages  
0      301 302 303 304 305 306 307 308 309 310 311 31...  
1      1056 1057 1058 1059 1060 60971 76515 76871 780...  
2      971 973 1166 1167 1168 1169 1170 1171 1172 117...  
3      1297 1300 1311 1312 1313 1314 1315 1316 1319 1...  
4      1

In [11]:
pages_per_categories_dict = dict(pages_per_categories.values.tolist())
pages_per_categories_dict

{'Buprestoidea': '301 302 303 304 305 306 307 308 309 310 311 312 313 314 315 316 317 318 319 320 321 322 323 324 325 326 327 328 329 330 331 332 333 334 335 336 337 338 339 340 341 342 343 344 345 346 347 348 349 350 351 352 353 354 355 356 357 358 359 360 361 362 363 364 365 366 367 368 369 370 371 372 373 374 375 376 377 378 379 380 381 382 383 384 385 386 387 388 389 390 391 392 393 394 395 396 397 398 399 400 401 402 403 404 405 406 407 408 409 410 411 412 413 414 415 416 417 418 419 420 421 422 423 424 425 426 427 428 429 430 431 432 433 434 435 436 437 438 439 440 441 442 443 444 445 446 447 448 449 450 451 452 453 454 455 456 457 458 459 460 461 462 463 464 465 466 467 468 469 470 471 472 473 474 475 476 477 478 479 480 481 482 483 484 485 486 487 488 489 490 491 492 493 494 495 496 497 498 499 500 501 502 503 504 505 506 507 508 509 510 511 512 513 514 515 516 517 518 519 520 521 522 523 524 525 526 527 528 529 530 531 532 533 534 535 536 537 538 539 540 541 542 543 544 545 54

#### Fix

You will notice that one article might belong to a single category or multiple ones.<br> In the case of multiple appearance, you break the ties uniformly at random.<br> Please, do it before solving any task in the homework.

In [12]:
# scrivere script per analizzare la colonna "pages". Se un numero è presente su più righe allora scegliere la categoria associata complatamente casualmente

In [33]:
# Append multiple value to a key in dictionary
def add_values_in_dict(sample_dict, key, list_of_values):
    """Append multiple values to a key in the given dictionary"""
    if key not in sample_dict:
        sample_dict[key] = list()
    sample_dict[key].extend(list_of_values)
    return sample_dict

In [34]:
articles_list = []
all_pages_list = []
pages_list = []
categorie_doppioni_list = [] 

separated_pages_per_categories_dict = {}

for key in pages_per_categories_dict:
    
    articles_list.append(key) #we'll use them as keys for the new dictionary
    
    if pages_per_categories_dict[key] != None:
    
        pages = pages_per_categories_dict[key].split(" ")
        #print(articles)
        
        pages_list.append(pages) #we'll use them as values for the new dictionary
        
        separated_pages_per_categories_dict = add_values_in_dict(separated_pages_per_categories_dict, key, pages)
        
        #let's create a list with all pages now
        if pages[0] == None:
            continue
        else:
            for page in pages:
                all_pages_list.append(page) 
                #all_pages_list contains all pages now   
                
                
        
#separated_pages_per_categories_dict = dict(zip(articles_list, pages_list))  

In [35]:
separated_pages_per_categories_dict

{'Buprestoidea': ['301',
  '302',
  '303',
  '304',
  '305',
  '306',
  '307',
  '308',
  '309',
  '310',
  '311',
  '312',
  '313',
  '314',
  '315',
  '316',
  '317',
  '318',
  '319',
  '320',
  '321',
  '322',
  '323',
  '324',
  '325',
  '326',
  '327',
  '328',
  '329',
  '330',
  '331',
  '332',
  '333',
  '334',
  '335',
  '336',
  '337',
  '338',
  '339',
  '340',
  '341',
  '342',
  '343',
  '344',
  '345',
  '346',
  '347',
  '348',
  '349',
  '350',
  '351',
  '352',
  '353',
  '354',
  '355',
  '356',
  '357',
  '358',
  '359',
  '360',
  '361',
  '362',
  '363',
  '364',
  '365',
  '366',
  '367',
  '368',
  '369',
  '370',
  '371',
  '372',
  '373',
  '374',
  '375',
  '376',
  '377',
  '378',
  '379',
  '380',
  '381',
  '382',
  '383',
  '384',
  '385',
  '386',
  '387',
  '388',
  '389',
  '390',
  '391',
  '392',
  '393',
  '394',
  '395',
  '396',
  '397',
  '398',
  '399',
  '400',
  '401',
  '402',
  '403',
  '404',
  '405',
  '406',
  '407',
  '408',
  '409',
  '

In [39]:
all_pages_list

['301',
 '302',
 '303',
 '304',
 '305',
 '306',
 '307',
 '308',
 '309',
 '310',
 '311',
 '312',
 '313',
 '314',
 '315',
 '316',
 '317',
 '318',
 '319',
 '320',
 '321',
 '322',
 '323',
 '324',
 '325',
 '326',
 '327',
 '328',
 '329',
 '330',
 '331',
 '332',
 '333',
 '334',
 '335',
 '336',
 '337',
 '338',
 '339',
 '340',
 '341',
 '342',
 '343',
 '344',
 '345',
 '346',
 '347',
 '348',
 '349',
 '350',
 '351',
 '352',
 '353',
 '354',
 '355',
 '356',
 '357',
 '358',
 '359',
 '360',
 '361',
 '362',
 '363',
 '364',
 '365',
 '366',
 '367',
 '368',
 '369',
 '370',
 '371',
 '372',
 '373',
 '374',
 '375',
 '376',
 '377',
 '378',
 '379',
 '380',
 '381',
 '382',
 '383',
 '384',
 '385',
 '386',
 '387',
 '388',
 '389',
 '390',
 '391',
 '392',
 '393',
 '394',
 '395',
 '396',
 '397',
 '398',
 '399',
 '400',
 '401',
 '402',
 '403',
 '404',
 '405',
 '406',
 '407',
 '408',
 '409',
 '410',
 '411',
 '412',
 '413',
 '414',
 '415',
 '416',
 '417',
 '418',
 '419',
 '420',
 '421',
 '422',
 '423',
 '424',
 '425',


In [40]:
#create a list with all the duplicates in articles_list
duplicates = [item for item, count in collections.Counter(all_pages_list).items() if count > 1]

In [41]:
duplicates

['303',
 '3574',
 '5319',
 '8220',
 '8587',
 '9348',
 '9440',
 '9495',
 '10053',
 '15516',
 '354224',
 '428725',
 '1297',
 '1300',
 '1311',
 '1312',
 '1313',
 '1314',
 '1315',
 '1316',
 '1319',
 '1320',
 '1322',
 '1323',
 '1324',
 '1325',
 '1326',
 '1327',
 '1329',
 '1330',
 '1332',
 '1333',
 '1334',
 '1335',
 '1336',
 '1337',
 '1338',
 '1339',
 '1341',
 '1342',
 '1343',
 '1345',
 '1346',
 '1349',
 '1351',
 '1352',
 '1353',
 '1354',
 '1356',
 '1357',
 '1358',
 '1359',
 '1361',
 '1363',
 '1364',
 '1365',
 '1366',
 '1367',
 '1368',
 '1371',
 '1372',
 '1374',
 '1375',
 '1376',
 '1377',
 '1378',
 '1380',
 '1383',
 '1385',
 '1387',
 '1390',
 '1393',
 '1395',
 '1403',
 '1404',
 '1410',
 '1418',
 '1427',
 '1429',
 '1431',
 '1435',
 '1440',
 '1441',
 '1446',
 '1455',
 '1461',
 '1466',
 '1473',
 '1513',
 '562072',
 '604876',
 '604884',
 '604888',
 '635747',
 '657073',
 '719336',
 '751685',
 '773402',
 '800357',
 '883789',
 '1002565',
 '1230384',
 '1627518',
 '1747657',
 '1754961',
 '1763149',
 

In [ ]:
duplicates_dict = {}

for duplicate in duplicates:

    list_of_keys = [key
                    for key, list_of_values in separated_pages_per_categories_dict.items()
                    if duplicate in list_of_values]
    
    duplicates_dict = add_values_in_dict(duplicates_dict, duplicate, list_of_keys)

In [55]:
duplicates_dict

{'303': ['Buprestoidea', 'Insect families'],
 '3574': ['Skin conditions resulting from physical factors', 'Tort law'],
 '5319': ['Skin conditions resulting from physical factors', 'Medical signs'],
 '8220': ['Skin conditions resulting from physical factors',
  '2000s fashion',
  '1990s fashion'],
 '8587': ['Skin conditions resulting from physical factors',
  'Medical emergencies'],
 '9348': ['Skin conditions resulting from physical factors',
  'Medical emergencies'],
 '9440': ['Skin conditions resulting from physical factors', 'Medical signs'],
 '9495': ['Skin conditions resulting from physical factors',
  'Medical emergencies'],
 '10053': ['Skin conditions resulting from physical factors',
  'Medical emergencies'],
 '15516': ['Skin conditions resulting from physical factors', 'Radioactivity']}

In [ ]:
#choose randomly just one value per key in the duplicates_dict dictionary

for key in duplicates_dict:
    for i in range(len(duplicates_dict[key]) - 1):
        random_item_from_list = random.choice(duplicates_dict[key])
        duplicates_dict[key].remove(random_item_from_list)
        
#now duplicate_dict is composed by articles and one page per article chosen randomly

In [ ]:
# update 
for key in separated_pages_per_categories_dict:
    
    for pages in separated_pages_per_categories_dict[key]: #accedo alla lista delle pagine nel separated_pages_per_categories_dict
        
        for page in pages: #accedo alle singole pagine nel dictionary separated_pages_per_categories_dict
        
            for dupl_key in duplicates_dict:
            
                for article in duplicates_dict[dupl_key]:
                
                    if page == dupl_key and key != article:
                        separated_pages_per_categories_dict[key].remove(page)